In [1]:
import pandas as pd
import os
from pathlib import Path
import plotly.graph_objects as go
import plotly.express as px
import seaborn as sns
import matplotlib.pyplot as plt
import geopandas as gpd
import requests
from itertools import chain
from shapely.geometry import Point, LineString, Polygon, MultiPolygon
import numpy as np

In [2]:
PATH_REPO_ROOT = Path().resolve().parent
PATH_DATA = PATH_REPO_ROOT / "data"
PATH_DATA_RAW = PATH_DATA / "raw"
PATH_DATA_RAW

PosixPath('/beegfs/.global0/ws/s4610340-energy_behavior/yahor/kaggle-predict_energy_behavior_of_prosumers/data/raw')

In [3]:
def order_ways(list_list_points):
    #list_first_points = [list_points[0] for list_points in list_list_points]
    #list_last_points = [list_points[-1] for list_points in list_list_points]
    ordered_list_list_points = []
    first_list_point = list_list_points[0]
    list_points = list_list_points[0]
    last_point = 0
    while (last_point != first_list_point[-1]):
        ordered_list_list_points.append(list_points)
        list_list_points.remove(list_points)
        list_first_points = [list_points[0] for list_points in list_list_points]
        list_last_points = [list_points[-1] for list_points in list_list_points]
        #print(list_points[0])
        #print(list_points[-1])
        #print()
        last_point = list_points[-1]
        try:
            index_list_points = list_first_points.index(last_point)
            list_points = list_list_points[index_list_points]
        except ValueError:
            try:
                index_list_points = list_last_points.index(last_point)
                list_points = list_list_points[index_list_points]
                list_points.reverse()
            except ValueError:
                break
        last_point = list_points[-1]
    return ordered_list_list_points

# create query
overpass_query_counties = """
[out:json];
area["name:en"="Estonia"]->.searchArea;
(
  relation["admin_level"="6"](area.searchArea);
);
out geom;
"""


# get Estonia boundaries from overpass
response = requests.post("https://overpass-api.de/api/interpreter", data=overpass_query_counties)
estonia_geojson = response.json()

# parse geometry
geometry = []
names = []
for element in estonia_geojson['elements']:
    members = element['members']
    name = element["tags"]["alt_name"]
    names.append(name)
    coords_poly = []
    for member in members:
        if member['type'] == 'way' and 'geometry' in member:
            coords = [(node['lon'], node['lat']) for node in member['geometry']]
            coords_poly.append(coords)
            #geometry.append(LineString(coords))
    coords_poly = order_ways(coords_poly)
    coords_poly = list(chain(*coords_poly))
    geometry.append(Polygon(coords_poly))

name_series = pd.Series(names, name="County")
gdf = gpd.GeoDataFrame(name_series, geometry=geometry)
gdf = gdf.set_index("County")
gdf.crs = 'EPSG:4326'
gdf


geometry
County                                                          
Saaremaa       POLYGON ((21.64083 58.74281, 21.60667 58.68833...
Pärnumaa       POLYGON ((24.06525 58.76243, 24.06507 58.76238...
Hiiumaa        POLYGON ((22.73333 59.29167, 22.60333 59.29500...
Läänemaa       POLYGON ((24.09365 58.98936, 24.10263 58.99037...
Ida-Virumaa    POLYGON ((26.79538 59.40712, 26.80395 59.40645...
Harjumaa       POLYGON ((24.16252 59.02535, 24.16657 59.02435...
Lääne-Virumaa  POLYGON ((26.79538 59.40712, 26.80395 59.40645...
Tartumaa       POLYGON ((26.67412 58.63174, 26.67416 58.63169...
Valgamaa       POLYGON ((26.05763 58.09585, 26.05499 58.09556...
Viljandimaa    POLYGON ((26.13354 58.38427, 26.13315 58.38399...
Põlvamaa       POLYGON ((27.55495 58.10111, 27.57292 58.10988...
Järvamaa       POLYGON ((25.06441 58.72932, 25.06455 58.72965...
Raplamaa       POLYGON ((25.05484 58.75262, 25.04740 58.75621...
Võrumaa        POLYGON ((27.55495 58.10111, 27.57292 58.10988...
Jõgevamaa      POLYGON ((26.72771 58.96770, 26.71828 58.96515...

In [4]:
# create query
overpass_query_land_area = """
[out:json];
area["name:en"="Estonia"]->.searchArea;
(
  relation[boundary=land_area][admin_level=2](area.searchArea);
);
out geom;
"""

# get Estonia boundaries from overpass
response = requests.post("https://overpass-api.de/api/interpreter", data=overpass_query_land_area)
land_area_geojson = response.json()

# parse geometry
geometry = []
members = land_area_geojson['elements'][0]['members']
coords_poly = []
for member in members:
    if member['type'] == 'way' and 'geometry' in member:
        coords = [(node['lon'], node['lat']) for node in member['geometry']]
        coords_poly.append(coords)
        #geometry.append(LineString(coords))
coords_poly = order_ways(coords_poly)
coords_poly = list(chain(*coords_poly))
geometry.append(Polygon(coords_poly))

gdf_land = gpd.GeoDataFrame(geometry=geometry)
gdf_land.crs = 'EPSG:4326'
gdf_land

geometry
0  POLYGON ((23.66113 58.97234, 23.66103 58.97236...

In [5]:
# create query
overpass_query_hiiumaa = """
[out:json];
area["name:en"="Estonia"]->.searchArea;
(
  relation[place=island][name="Hiiumaa"](area.searchArea);
);
out geom;
"""

# get Estonia boundaries from overpass
response = requests.post("https://overpass-api.de/api/interpreter", data=overpass_query_hiiumaa)
hiiumaa_geojson = response.json()

# parse geometry
geometry = []
members = hiiumaa_geojson['elements'][0]['members']
coords_poly = []
for member in members:
    if member['type'] == 'way' and 'geometry' in member:
        coords = [(node['lon'], node['lat']) for node in member['geometry']]
        coords_poly.append(coords)
        #geometry.append(LineString(coords))
coords_poly = order_ways(coords_poly)
coords_poly = list(chain(*coords_poly))
geometry.append(Polygon(coords_poly))

gdf_hiiumaa = gpd.GeoDataFrame(geometry=geometry)
gdf_hiiumaa.crs = 'EPSG:4326'
gdf_hiiumaa

geometry
0  POLYGON ((22.50372 58.69849, 22.50380 58.69846...

In [6]:
# create query
overpass_query_saaremaa = """
[out:json];
area["name:en"="Estonia"]->.searchArea;
(
  relation[place=island][name="Saaremaa"](area.searchArea);
);
out geom;
"""

# get Estonia boundaries from overpass
response = requests.post("https://overpass-api.de/api/interpreter", data=overpass_query_saaremaa)
saaremaa_geojson = response.json()

# parse geometry
geometry = []
members = saaremaa_geojson['elements'][0]['members']
coords_poly = []
for member in members:
    if member['type'] == 'way' and 'geometry' in member:
        coords = [(node['lon'], node['lat']) for node in member['geometry']]
        coords_poly.append(coords)
        #geometry.append(LineString(coords))
coords_poly = order_ways(coords_poly)
coords_poly = list(chain(*coords_poly))
geometry.append(Polygon(coords_poly))

gdf_saaremaa = gpd.GeoDataFrame(geometry=geometry)
gdf_saaremaa.crs = 'EPSG:4326'

gdf_saaremaa

geometry
0  POLYGON ((22.03950 58.00463, 22.03944 58.00450...

In [8]:
df_weather_hist = pd.read_csv(PATH_DATA_RAW / "historical_weather.csv")

unique_coords_forecast = np.unique(df_weather_hist[["latitude", "longitude"]], axis=0)
points = [Point(x, y) for y, x in unique_coords_forecast]
points_gdf = gpd.GeoDataFrame(points, columns=['geometry'])
points_gdf

for county in gdf.index:
    points_gdf[county] = points_gdf.apply(lambda x: x.geometry.within(gdf.loc[county, "geometry"]), axis=1)

points_gdf["county"] = points_gdf[gdf.index].apply(lambda x: x[x].index[0] if len(x[x]) > 0 else False, axis=1)
points_gdf["land"] = points_gdf.apply(lambda x: x.geometry.within(gdf_land.loc[0, "geometry"]), axis=1)
points_gdf["saaremaa"] = points_gdf.apply(lambda x: x.geometry.within(gdf_saaremaa.loc[0, "geometry"]), axis=1)
points_gdf["hiiumaa"] = points_gdf.apply(lambda x: x.geometry.within(gdf_hiiumaa.loc[0, "geometry"]), axis=1)
points_gdf["land"] = points_gdf["land"] | points_gdf["saaremaa"] | points_gdf["hiiumaa"]
points_gdf["county"] = points_gdf["county"] * points_gdf["land"]
points_gdf["county"] = points_gdf["county"].replace(["", 0], np.nan)
points_gdf = points_gdf[["geometry", "county"]]
points_gdf.loc[50:60]

geometry       county
50  POINT (25.70000 58.50000)  Viljandimaa
51  POINT (26.20000 58.50000)    Jõgevamaa
52  POINT (26.70000 58.50000)     Tartumaa
53  POINT (27.20000 58.50000)     Tartumaa
54  POINT (27.70000 58.50000)          NaN
55  POINT (28.20000 58.50000)          NaN
56  POINT (21.70000 58.80000)          NaN
57  POINT (22.20000 58.80000)          NaN
58  POINT (22.70000 58.80000)      Hiiumaa
59  POINT (23.20000 58.80000)          NaN
60  POINT (23.70000 58.80000)     Läänemaa

In [10]:
df_weather_hist

datetime  temperature  dewpoint  rain  snowfall  \
0        2021-09-01 00:00:00         14.2      11.6   0.0       0.0   
1        2021-09-01 00:00:00         13.9      11.5   0.0       0.0   
2        2021-09-01 00:00:00         14.0      12.5   0.0       0.0   
3        2021-09-01 00:00:00         14.6      11.5   0.0       0.0   
4        2021-09-01 00:00:00         15.7      12.9   0.0       0.0   
...                      ...          ...       ...   ...       ...   
1710797  2023-05-30 10:00:00         11.7       4.6   0.0       0.0   
1710798  2023-05-30 10:00:00         12.3       3.5   0.0       0.0   
1710799  2023-05-30 10:00:00          9.8       3.0   0.0       0.0   
1710800  2023-05-30 10:00:00         11.7       1.6   0.0       0.0   
1710801  2023-05-30 10:00:00         12.0       1.4   0.0       0.0   

         surface_pressure  cloudcover_total  cloudcover_low  cloudcover_mid  \
0                  1015.9                31              31               0   
1                  1010.7                33              37               0   
2                  1015.0                31              34               0   
3                  1017.3                 0               0               0   
4                  1014.0                22              25               0   
...                   ...               ...             ...             ...   
1710797            1018.9                40               9              54   
1710798            1019.0                46               4              70   
1710799            1019.2                41               4              62   
1710800            1019.0                44               0              73   
1710801            1016.1                38               0              63   

         cloudcover_high  windspeed_10m  winddirection_10m  \
0                     11       7.083333                  8   
1                      0       5.111111                359   
2                      0       6.333333                355   
3                      0       8.083333                297   
4                      0       8.416667                  5   
...                  ...            ...                ...   
1710797                0       1.055556                253   
1710798                0       0.805556                263   
1710799                0       1.972222                285   
1710800                0       3.500000                307   
1710801                0       3.250000                304   

         shortwave_radiation  direct_solar_radiation  diffuse_radiation  \
0                        0.0                     0.0                0.0   
1                        0.0                     0.0                0.0   
2                        0.0                     0.0                0.0   
3                      358.0                   277.0               81.0   
4                        0.0                     0.0                0.0   
...                      ...                     ...                ...   
1710797                567.0                   392.0              175.0   
1710798                581.0                   407.0              174.0   
1710799                609.0                   432.0              177.0   
1710800                658.0                   521.0              137.0   
1710801                672.0                   550.0              122.0   

         latitude  longitude  data_block_id  
0            57.6       21.7            1.0  
1            57.6       22.2            1.0  
2            57.6       22.7            1.0  
3            57.6       23.2            1.0  
4            57.6       23.7            1.0  
...           ...        ...            ...  
1710797      59.7       26.2          637.0  
1710798      59.7       26.7          637.0  
1710799      59.7       27.2          637.0  
1710800      59.7       27.7          637.0  
1710801      59.7       28.2          637.0  

[1710802 rows x 18 

In [25]:
from pydantic_core import to_json
from shapely import to_geojson
import json

fig = go.Figure()

trace_county_centers = go.Scattermapbox(
    lon=gdf.to_crs('+proj=cea').centroid.to_crs(gdf.crs).x,
    lat=gdf.to_crs('+proj=cea').centroid.to_crs(gdf.crs).y,
    hovertext=gdf.index,
    mode = 'markers',
    marker = dict(
        color = "grey",
        size = 15,
    ),
    name="County centers"
)

trace_weather_stations = go.Scattermapbox(
    lat=np.unique(df_weather_hist[["latitude", "longitude"]], axis=0)[:, 0],
    lon=np.unique(df_weather_hist[["latitude", "longitude"]], axis=0)[:, 1],
    mode = 'markers',
    hoverinfo="skip",
    name="Weather stations"
)

fig.add_traces([trace_county_centers, trace_weather_stations])

fig.update_mapboxes(
    style="open-street-map",
    layers=[
        {
            "source": json.loads(gdf["geometry"].to_json()),
            "below": "traces",
            "type": "line",
            "color": "grey",
            "line": {"width": 1.5},
        }
    ],
    center=dict(
        lat=gdf.to_crs('+proj=cea').centroid.to_crs(gdf.crs).iloc[0].coords[0][1],
        lon=gdf.to_crs('+proj=cea').centroid.to_crs(gdf.crs).iloc[0].coords[0][0]
    ),
    zoom=5
)

fig.update_layout(height=800)


fig.show()